In [ ]:
'''
Обработка текста предвыборных программ.

Цели:
    частотный анализ текста
    распределить кандидатов по категориям (культмасс, правозащита, неопределившиеся)

'''

In [ ]:
# векторный анализ текста:
#     посчитать частотность слов в тексте, нормировать по евклидовой норме (СДЕЛАТЬ ЭТО ПО СОЗЫВАМ)
#     убрать союзы, предлоги и тд
'''
документ = программа
коллекция = программы за один созыв

или

документ = программы за один созыв
коллекция = программы за все созывы

классификация текстов регрессией:
    распределить кандидатов по классам (культмасс, правозащита, неопределившиеся)

'''

In [91]:
import pandas as pd
import re
import numpy as np

In [10]:
programs_df = pd.read_csv('library: main/ssmm_elections_candidates_1_11.csv', sep='\t', encoding='utf-8')
programs_df = programs_df[['conv_x_name','program_txt']][programs_df['program_txt'].notna()].reset_index().drop(['index'],axis=1)
programs_df.head()

conv_x_name                                        program_txt
0      1_Левин_Андрей  Активный участник и организатор различных меро...
1  1_Кириллова_Полина  Мне нравится заниматься общественной деятельно...
2     1_Семенов_Павел  "Здравствуйте. Я так понимаю, что я уже поздно...
3   1_Кузнецова_Алёна  "Меня очень интересует жизнь Университета. я б...
4    1_Кунденко_Вадим  "   Добрый день! Пару слов о себе. Путь к мехм...

## 1. To create 1-token list and to remain only meaningful words

In [99]:
# to create a list of words from all programs

token_list = []
tokenize_regex = re.compile(r'([\w\-]+)', re.I)

for i in range(len(programs_df)):
    test_txt = programs_df['program_txt'][i]
    tokens = tokenize_regex.findall(test_txt)
    token_list += [str.lower(t) for t in tokens]
    
# print(token_list)

# немного отредактировать из-за -
token_list = [w for w in token_list if w[0] != '-'] + [w[1:] for w in token_list if w[0] == '-']

print(token_list)


['активный', 'участник', 'и', 'организатор', 'различных', 'мероприятий', 'воспоминания', 'о', 'любимой', 'школе', 'готов', 'работать', 'творить', 'уверен', 'что', 'все', 'получится', 'мне', 'нравится', 'заниматься', 'общественной', 'деятельностью', 'всячески', 'пытаюсь', 'расширять', 'свой', 'кругозор', 'еще', 'в', 'школе', 'организовывала', 'различные', 'мероприятия', 'и', 'была', 'сильно', 'этим', 'заинтересована', 'увлекаюсь', 'музыкой', 'для', 'большего', 'развития', 'записалась', 'в', 'академический', 'хор', 'начала', 'заниматься', 'спортивными', 'бальными', 'танцами', 'но', 'в', 'спорте', 'симпатизирую', 'футболу', 'планирую', 'посетить', 'еще', 'некоторые', 'клубы', 'университета', 'и', 'найти', 'что', 'также', 'может', 'меня', 'затянуть', 'хотелось', 'бы', 'внести', 'свой', 'клад', 'в', 'развитие', 'университета', 'план', 'работы', '1', 'всестороннее', 'развитие', 'студентов', 'нас', 'кругом', 'окружает', 'бескультурье', 'и', 'невежество', 'общество', 'просто', 'гниет', 'многие

In [100]:
# to create a dictionary with word counter

token_dict = {}
for w in token_list:
    token_dict[w] = {'type': '', 'parent': '', 'cnt': 0}
    
for w in token_list:
    token_dict[w]['cnt'] += 1

token_dict = dict(sorted(token_dict.items(), key=lambda item: item[1]['cnt'], reverse=True))
token_dict

{'в': {'type': '', 'parent': '', 'cnt': 1862},
 'и': {'type': '', 'parent': '', 'cnt': 1577},
 'я': {'type': '', 'parent': '', 'cnt': 891},
 'на': {'type': '', 'parent': '', 'cnt': 663},
 'с': {'type': '', 'parent': '', 'cnt': 458},
 'не': {'type': '', 'parent': '', 'cnt': 443},
 'что': {'type': '', 'parent': '', 'cnt': 410},
 'по': {'type': '', 'parent': '', 'cnt': 328},
 'для': {'type': '', 'parent': '', 'cnt': 254},
 'меня': {'type': '', 'parent': '', 'cnt': 243},
 'а': {'type': '', 'parent': '', 'cnt': 230},
 'бы': {'type': '', 'parent': '', 'cnt': 220},
 'мехмата': {'type': '', 'parent': '', 'cnt': 220},
 'как': {'type': '', 'parent': '', 'cnt': 218},
 'это': {'type': '', 'parent': '', 'cnt': 202},
 'за': {'type': '', 'parent': '', 'cnt': 200},
 'хочу': {'type': '', 'parent': '', 'cnt': 198},
 'но': {'type': '', 'parent': '', 'cnt': 185},
 'о': {'type': '', 'parent': '', 'cnt': 181},
 'мне': {'type': '', 'parent': '', 'cnt': 178},
 'студентов': {'type': '', 'parent': '', 'cnt': 16

In [67]:
# предлоги
prepositions_list = [
    # Классификация по происхождению и строению
# Непроизводные (древнейшие предлоги) — 
    'в', 'без', 'до', 'из', 'к', 'на', 'по', 'о', 'от', 'перед', 'при', 'через', 'с', 'у', 'за', 'над', 'об', 'обо', 'под', 'про', 'для',
# Производные предлоги образовались в более позднее время от слов других частей речи и подразделяются на:
# наречные — 
    'вблизи', 'вглубь', 'вдоль', 'возле', 'около', 'вокруг', 'впереди', 'после',
# отымённые — 
    'посредством', 'путём', 'путем', 'насчёт', 'насчет', 'ввиду', # в роли, в зависимости от, по поводу, по случаю, в течение и др.;
# глагольные (образованы были в большинстве своём скорее от деепричастий, нежели собственно глаголов) — 
    'благодаря', 'спустя', # несмотря на, 

    # Классификация по структуре
# Простые (состоят из одного слова): 
    'в', 'с', 'со', 'к', 'у', 'над', 'на', 'перед', 'при',
# сложные (состоят из двух простых, соединённых дефисом): 
    'из-под', 'из-за', 'по-над',
# составные (состоят из нескольких слов): 
#     несмотря на, в отличие от, в связи с, 

    # Классификация по употреблению с падежами существительных (валентность)
# с одним падежом: 
    'без', 'до', 'для', 'у', 'ради', 'к', 'про', 'через', 'сквозь', 'над', 'перед', 'при',
# с двумя падежами: 
    'в', 'на', 'о', 'между', 'за', 'под',
# с тремя падежами: 
    'по', 'с',

    # Классификация по отношениям
# пространственные — 
    'около', 'в', 'среди', 'на',
# временные — 
#     в течение, в продолжение и др.;
# причинные — 
    'ввиду', 'благодаря', 'вследствие', # в связи, из-за и др.;
# целевые — 
   'для',
# объектные — 
    'о',
# уступки — 
#     несмотря на
    
    
    'вне',
    ''
]

# союзы
conjunctions_list = [
    'и', 'да', 'или', 'либо', 'ли', 'а', 'да', 'но', 'зато', 'однако', 'же', 'тоже', 'также', 
    'притом', 'причём', 'причем', 'именно', 'что', 'чтобы', 'чтоб', 'как', 
    'когда', 'лишь', 'едва', 'где', 'куда', 'откуда', 'столько', 'настолько', 'так', 'такой', # до такой степени, до того,  
    'как', 'словно', 'будто', 'точно', 'если', 'коли', 'ежели', # как будто, как бы, так как, потому что, если бы, 
    'что', 'хотя', 'хоть', 'пускай', 'чтобы', 'дабы', # несмотря на то, с тем чтобы, так что
    'только', 
    ''
#     то есть
#     т.е.
    
#     сочинительные:
# соединительные (и, да (= и), не только … но и, также, тоже, и … и, ни … ни, как … так и, сколько … столько и)
# разделительные (или, или … или, либо, либо … либо, то … то, то ли … то ли, не то … не то)
# противительные (а, да (= но), но, зато, однако, же, однако же, все же)
# градационные (не только… но и, не столько… сколько, не то чтобы… а)
# присоединительные (тоже, также, да и, и, притом, причём)
# пояснительные (то есть, а именно)

    # подчинительные:
# изъяснительные (что, чтобы, как, …)

    # обстоятельственные
# времени (когда, лишь, едва, …)
# места (где, куда, откуда, …)
# образа действия, меры, степени (столько, настолько, так, до такой степени, до того, такой, …)
# сравнения (как, как будто, словно, будто, точно, как бы)
# причины (так как, потому что, …)
# условия (если, если бы, коли, ежели, если … то,…)
# уступки (несмотря на то, что, хотя, хоть, пускай, …)
# цели (чтобы, дабы, с тем чтобы, …)
# следствия (так что)
    
]

# местоимения
pronouns_list = [
    'я', 'меня', 'мне', 'меня', 'мной', 'мною', 
    'ты', 'тебя', 'тебе', 'тебя', 'тобой', 'тобою', 
    'он', 'оно', 'его', 'него', 'ему', 'нему', 'им', 'ним', 'нём', 'нем',
    'она', 'её', 'ее', 'неё', 'нее', 'ей', 'ней', 'ею', 'нею',
    'кто', 'что', 'какой', 'каков', 'чей', 'который', 'этот', 'эта', 'это', 'эти', 'тот', 'та', 'то', 'те', 
    'такой', 'такая', 'такое', 'такие', 'таков', 'такова', 'таково', 'таковы', 'сей', 'сия', 'сие', 'сии',
    'все', 'весь', 'всяк', 'всякий', 'любой', 'каждый', 'сам', 'самый', 'другой', 'иной', 
    'никто', 'ничто', 'некого', 'нечего', 'нисколько', 'никакой', 'ничей', 'некто', 'нечто', 'некий', 'некоторый', 'несколько',
    
#     разное
    'себе', 'нашего', 'том', 'всех', 'себя', 'всё', 'которые', 'всего', 'этом', 'почему', 'что-то', 'помимо', 
    'них', 'свою', 'потому', 'эту', 'даже', 'тем', 'этой', 'ещё', 'еще', 'здесь', 'вы', 'этим', 'всем', 'ведь', 'той', 
    'во-первых', 'во-вторых', 'в-третьих', 'моя', 'всему', 'кое-какие', 'никак', 'наших', 'моё', 'всё-таки', 'наша', 'мои', 
    'вашу', 'своим', 'кем', 'там', 'чего', 'кого', 'моей', 'ваши', 'вот', 'своей', 'таких', 'другие', 'как-то', 'свои',
    'сама', 'этого', 'нашем', 'теми', 'кому', 'свой', 'тот', 'сей', 'сей', 'нас', 'своё',
    ''
#     неопределённые местоимения с приставкой кое- или постфиксами -то, -либо, -нибудь
]

# наречия
adverbs_list = [
    'только', 'поэтому', 'очень', 'более',
    ''
]

# частицы
particles_list = [
    'бишь', 'бы', 'да', 'де', 'дескать', 'же', 'ишь', 'не', 'небось', 'нет', 'неужели', 'нехай', 'ни', 'таки', 'уж'
#     -ка, -то
]

# другой мусор
garbage_list = [
    '-', '1', '2', '3', '4', '5', '6', '', '', '', '', '', '', ''
]

full_gabage_list = prepositions_list + conjunctions_list + pronouns_list + adverbs_list + particles_list + garbage_list


In [101]:
def part_of_speech(token_list):
    for w in token_list:
        if w in prepositions_list:
            token_dict[w]['type'] = 'preposition'
        elif w in conjunctions_list:
            token_dict[w]['type'] = 'conjunction'
        elif w in pronouns_list:
            token_dict[w]['type'] = 'pronoun'
        elif w in adverbs_list:
            token_dict[w]['type'] = 'adverb'
        elif w in particles_list:
            token_dict[w]['type'] = 'particle'
        elif w in garbage_list:
            token_dict[w]['type'] = 'garbage'
        else:
            token_dict[w]['type'] = 'meaningful'
    return token_dict

part_of_speech(token_dict)

{'в': {'type': 'preposition', 'parent': '', 'cnt': 1862},
 'и': {'type': 'conjunction', 'parent': '', 'cnt': 1577},
 'я': {'type': 'pronoun', 'parent': '', 'cnt': 891},
 'на': {'type': 'preposition', 'parent': '', 'cnt': 663},
 'с': {'type': 'preposition', 'parent': '', 'cnt': 458},
 'не': {'type': 'particle', 'parent': '', 'cnt': 443},
 'что': {'type': 'conjunction', 'parent': '', 'cnt': 410},
 'по': {'type': 'preposition', 'parent': '', 'cnt': 328},
 'для': {'type': 'preposition', 'parent': '', 'cnt': 254},
 'меня': {'type': 'pronoun', 'parent': '', 'cnt': 243},
 'а': {'type': 'conjunction', 'parent': '', 'cnt': 230},
 'бы': {'type': 'particle', 'parent': '', 'cnt': 220},
 'мехмата': {'type': 'meaningful', 'parent': '', 'cnt': 220},
 'как': {'type': 'conjunction', 'parent': '', 'cnt': 218},
 'это': {'type': 'pronoun', 'parent': '', 'cnt': 202},
 'за': {'type': 'preposition', 'parent': '', 'cnt': 200},
 'хочу': {'type': 'meaningful', 'parent': '', 'cnt': 198},
 'но': {'type': 'conjunc

In [102]:
meaningful_token_dict = {w: token_dict[w] for w in token_dict if token_dict[w]['type'] == 'meaningful'}
meaningful_token_dict

{'мехмата': {'type': 'meaningful', 'parent': '', 'cnt': 220},
 'хочу': {'type': 'meaningful', 'parent': '', 'cnt': 198},
 'студентов': {'type': 'meaningful', 'parent': '', 'cnt': 167},
 'студсовет': {'type': 'meaningful', 'parent': '', 'cnt': 158},
 'студсовета': {'type': 'meaningful', 'parent': '', 'cnt': 157},
 'уже': {'type': 'meaningful', 'parent': '', 'cnt': 142},
 'факультета': {'type': 'meaningful', 'parent': '', 'cnt': 139},
 'привет': {'type': 'meaningful', 'parent': '', 'cnt': 137},
 'организации': {'type': 'meaningful', 'parent': '', 'cnt': 133},
 'мероприятий': {'type': 'meaningful', 'parent': '', 'cnt': 124},
 'студсовете': {'type': 'meaningful', 'parent': '', 'cnt': 124},
 'мгу': {'type': 'meaningful', 'parent': '', 'cnt': 115},
 'году': {'type': 'meaningful', 'parent': '', 'cnt': 107},
 'группы': {'type': 'meaningful', 'parent': '', 'cnt': 102},
 'их': {'type': 'meaningful', 'parent': '', 'cnt': 101},
 'есть': {'type': 'meaningful', 'parent': '', 'cnt': 100},
 'день': {'

In [18]:
# в parent положить инфинитивную форму слов

# pip install pymorphy2
# https://pymorphy2.readthedocs.io/en/latest/user/guide.html#inflection
    
import pymorphy2
morph = pymorphy2.MorphAnalyzer()

In [13]:
# kek = morph.parse('студсовет')[0]
# gent = kek.inflect({'gent'})
# gent.word

In [14]:
# morph.parse('думающему')[0].normal_form

In [15]:
# morph.parse('думающему')[0].inflect({'sing', 'nomn'}).word

In [104]:

for w in meaningful_token_dict:
    meaningful_token_dict[w]['parent'] = morph.parse(w)[0].normal_form
    
meaningful_token_dict

{'мехмата': {'type': 'meaningful', 'parent': 'мехмат', 'cnt': 220},
 'хочу': {'type': 'meaningful', 'parent': 'хотеть', 'cnt': 198},
 'студентов': {'type': 'meaningful', 'parent': 'студент', 'cnt': 167},
 'студсовет': {'type': 'meaningful', 'parent': 'студсовет', 'cnt': 158},
 'студсовета': {'type': 'meaningful', 'parent': 'студсовет', 'cnt': 157},
 'уже': {'type': 'meaningful', 'parent': 'уже', 'cnt': 142},
 'факультета': {'type': 'meaningful', 'parent': 'факультет', 'cnt': 139},
 'привет': {'type': 'meaningful', 'parent': 'привет', 'cnt': 137},
 'организации': {'type': 'meaningful', 'parent': 'организация', 'cnt': 133},
 'мероприятий': {'type': 'meaningful', 'parent': 'мероприятие', 'cnt': 124},
 'студсовете': {'type': 'meaningful', 'parent': 'студсовет', 'cnt': 124},
 'мгу': {'type': 'meaningful', 'parent': 'мгу', 'cnt': 115},
 'году': {'type': 'meaningful', 'parent': 'год', 'cnt': 107},
 'группы': {'type': 'meaningful', 'parent': 'группа', 'cnt': 102},
 'их': {'type': 'meaningful',

## 2. To calculate weights for 1-TOKENS

In [105]:
# statistics of infinitive form of 1-tokens - for custom definition of branch 1-token lists

parent_token_dict = {}

for w in meaningful_token_dict:
    parent_token_dict[meaningful_token_dict[w]['parent']] = 0
for w in meaningful_token_dict:
    parent_token_dict[meaningful_token_dict[w]['parent']] += meaningful_token_dict[w]['cnt']
    
parent_token_dict = dict(sorted(parent_token_dict.items(), key=lambda x: x[1], reverse=True))
parent_token_dict


{'студсовет': 467,
 'быть': 405,
 'мехмат': 355,
 'хотеть': 303,
 'студент': 302,
 'год': 280,
 'группа': 277,
 'факультет': 266,
 'организация': 225,
 'мероприятие': 221,
 'студенческий': 213,
 'работа': 207,
 'совет': 189,
 'вопрос': 187,
 'жизнь': 186,
 'проблема': 176,
 'заниматься': 165,
 'помогать': 152,
 'день': 145,
 'уже': 142,
 'они': 139,
 'праздник': 139,
 'привет': 137,
 'сделать': 132,
 'человек': 131,
 'курс': 130,
 'участвовать': 120,
 'время': 116,
 'мгу': 115,
 'рабочий': 115,
 'который': 114,
 'деятельность': 111,
 'проект': 109,
 'мы': 107,
 'есть': 100,
 'участие': 100,
 'мочь': 99,
 'хотеться': 94,
 'идея': 90,
 'хороший': 90,
 'образование': 89,
 'новый': 89,
 'работать': 88,
 'созыв': 80,
 'вы': 77,
 'активный': 77,
 'помочь': 76,
 'тот': 74,
 'университет': 74,
 'планировать': 73,
 'наш': 73,
 'бытовой': 73,
 'являться': 72,
 'много': 70,
 'различный': 70,
 'один': 70,
 'решение': 69,
 'первый': 69,
 'интересный': 68,
 'член': 67,
 'проведение': 67,
 'стать': 6

In [106]:

# добавляем всевозможные вариации по общей родительской форме
def full_list_of_tokens_for_branch(token_dict, branch_parent_tokens):
    full_list_of_tokens = []
    for w in token_dict:
        if token_dict[w]['parent'] in branch_parent_tokens:
            full_list_of_tokens.append(w)
    return full_list_of_tokens


cultmass_tokens = ['мероприятие', 'праздник', 'пифагор', 'конкурс', 'посвящение', 'культурно-массовый', 'посвятой']
sport_tokens = ['спорт', 'чемпионат', 'футбол']

rights_fight_tokens = ['решение', 'решить', 'проблема', 'самоуправление', 'право', 'бороться', 'вопрос', 'помогать']

education_tokens = ['образование']
infrastructure_tokens = ['бытовой', 'проживание', 'макулатура', 'общежитие']
inform_tokens = ['оповещение', 'оповещать', 'информирование']

full_cultmass_tokens       = full_list_of_tokens_for_branch(meaningful_token_dict, cultmass_tokens)
full_sport_tokens          = full_list_of_tokens_for_branch(meaningful_token_dict, sport_tokens)
full_rights_fight_tokens   = full_list_of_tokens_for_branch(meaningful_token_dict, rights_fight_tokens)
full_education_tokens      = full_list_of_tokens_for_branch(meaningful_token_dict, education_tokens)
full_infrastructure_tokens = full_list_of_tokens_for_branch(meaningful_token_dict, infrastructure_tokens)
full_inform_tokens         = full_list_of_tokens_for_branch(meaningful_token_dict, inform_tokens)

# удалить неоднозначные варианты
full_rights_fight_tokens.remove('решил')
full_rights_fight_tokens.remove('решила')

# print('full_cultmass_tokens:', full_cultmass_tokens)
# print('full_sport_tokens:', full_sport_tokens)
# print('full_rights_fight_tokens:', full_rights_fight_tokens)
# print('full_education_tokens:', full_education_tokens)
# print('full_infrastructure_tokens:', full_infrastructure_tokens)
# print('full_inform_tokens:', full_inform_tokens)

In [108]:
conv_x_name_token_dict = {}

for i in range(len(programs_df)):
    tokens = tokenize_regex.findall(programs_df['program_txt'][i])
    conv_x_name_token_dict[programs_df['conv_x_name'][i]] = [str.lower(t) for t in tokens]
    conv_x_name_token_dict[programs_df['conv_x_name'][i]] = [w for w in conv_x_name_token_dict[programs_df['conv_x_name'][i]] if w[0] != '-'] + [w[1:] for w in conv_x_name_token_dict[programs_df['conv_x_name'][i]] if w[0] == '-']
    
print(conv_x_name_token_dict)


{'1_Левин_Андрей': ['активный', 'участник', 'и', 'организатор', 'различных', 'мероприятий', 'воспоминания', 'о', 'любимой', 'школе', 'готов', 'работать', 'творить', 'уверен', 'что', 'все', 'получится'], '1_Кириллова_Полина': ['мне', 'нравится', 'заниматься', 'общественной', 'деятельностью', 'всячески', 'пытаюсь', 'расширять', 'свой', 'кругозор', 'еще', 'в', 'школе', 'организовывала', 'различные', 'мероприятия', 'и', 'была', 'сильно', 'этим', 'заинтересована', 'увлекаюсь', 'музыкой', 'для', 'большего', 'развития', 'записалась', 'в', 'академический', 'хор', 'начала', 'заниматься', 'спортивными', 'бальными', 'танцами', 'но', 'в', 'спорте', 'симпатизирую', 'футболу', 'планирую', 'посетить', 'еще', 'некоторые', 'клубы', 'университета', 'и', 'найти', 'что', 'также', 'может', 'меня', 'затянуть', 'хотелось', 'бы', 'внести', 'свой', 'клад', 'в', 'развитие', 'университета', 'план', 'работы', '1', 'всестороннее', 'развитие', 'студентов', 'нас', 'кругом', 'окружает', 'бескультурье', 'и', 'невежест

In [53]:
# conv_x_name_token_dict['2014_Глунчадзе_Ираклий_Вахтангович']
# programs_df['program_txt'][programs_df.year_no_x_name == '2014_Глунчадзе_Ираклий_Вахтангович']

# kek = programs_df[programs_df.year_no_x_name == '2014_Глунчадзе_Ираклий_Вахтангович']
# kek['program_txt'][23]


In [125]:
# считаем, сколько ключевых слов по каждому направлению встретилось в программе кандидата

def get_flag_by_tokens(conv_x_name_token_dict, year_no_x_name, full_branch_tokens):
    branch_flg = 0
    for t in conv_x_name_token_dict[year_no_x_name]:
        if t in full_branch_tokens:
            branch_flg += 1
    return branch_flg


conv_x_name_weights = {}

for w in conv_x_name_token_dict:
    cultmass_w       = get_flag_by_tokens(conv_x_name_token_dict, w, full_cultmass_tokens)
    sport_w          = get_flag_by_tokens(conv_x_name_token_dict, w, full_sport_tokens)
    rights_fight_w   = get_flag_by_tokens(conv_x_name_token_dict, w, full_rights_fight_tokens)
    education_w      = get_flag_by_tokens(conv_x_name_token_dict, w, full_education_tokens)
    infrastructure_w = get_flag_by_tokens(conv_x_name_token_dict, w, full_infrastructure_tokens)
    inform_w         = get_flag_by_tokens(conv_x_name_token_dict, w, full_inform_tokens)
    
    conv_x_name_weights[w] = {
        'cultmass_w': cultmass_w, 
        'sport_w': sport_w, 
        'rights_fight_w': rights_fight_w, 
        'education_w': education_w, 
        'infrastructure_w': infrastructure_w, 
        'inform_w': inform_w
    }

# convocation_name_x_flags
conv_x_name_weights_df = pd.DataFrame(conv_x_name_weights).transpose()
conv_x_name_weights_df

cultmass_w  sport_w  rights_fight_w  \
1_Левин_Андрей                                    1        0               0   
1_Кириллова_Полина                                4        2               4   
1_Семенов_Павел                                   2        0               5   
1_Кузнецова_Алёна                                 2        0               1   
1_Кунденко_Вадим                                  0        0               2   
...                                             ...      ...             ...   
11_Терехов_Михаил_Сергеевич                       0        0               0   
11_Поликарпов_Александр_Валерьевич                0        0               0   
11_Каляев_Тимур_Джанбулатович                     0        0               2   
11_Маммагаджиев_Руслан_Гаджимагомедович           0        0               1   
11_Третьякова_Екатерина_Алексеевна                0        0               1   

                                         education_w  infrastructure_w  \
1_Левин_Андрей                                     0                 0   
1_Кириллова_Полина                                 0                 3   
1_Семенов_Павел                                    0                 3   
1_Кузнецова_Алёна                                  0                 0   
1_Кунденко_Вадим                                   0                 0   
...                                              ...               ...   
11_Терехов_Михаил_Сергеевич                        0                 0   
11_Поликарпов_Александр_Валерьевич                 0                 0   
11_Каляев_Тимур_Джанбулатович                      0                 0   
11_Маммагаджиев_Руслан_Гаджимагомедович            0                 0   
11_Третьякова_Екатерина_Алексеевна                 0                 0   

                                         inform_w  
1_Левин_Андрей                                  0  
1_Кириллова_Полина                              0  
1_Семенов_Павел                                 0  
1_Кузнецова_Алёна                               0  
1_Кунденко_Вадим                                0  
...                                           ...  
11_Терехов_Михаил_Сергеевич                     0  
11_Поликарпов_Александр_Валерьевич              0  
11_Каляев_Тимур_Джанбулатович                   0  
11_Маммагаджиев_Руслан_Гаджимагомедович         0  
11_Третьякова_Екатерина_Алексеевна              0  

[462 rows x 6 columns]

## 3. To calculate weights for  2-TOKENS

In [ ]:
# 2-токены

# сделать поиск 2-токенов и т.д., чтобы выявлять "студсовет МГУ", "университетском уровне" и прочее (на примере Глунчадзе)

In [110]:
# to remove all words except meaningful

conv_x_name_token_dict_meaningful = {}

for name in conv_x_name_token_dict:
    conv_x_name_token_dict_meaningful[name] = [word for word in conv_x_name_token_dict[name] if word in meaningful_token_dict.keys()]
    
# convocation_name_x_token_dict_meaningful['1_Тропин_Александр_Михайлович']


In [111]:
# to replace every word by its parent word

conv_x_name_token_dict_meaningful_parent = {}

for name in conv_x_name_token_dict:
    conv_x_name_token_dict_meaningful_parent[name] = [meaningful_token_dict[word]['parent'] for word in conv_x_name_token_dict_meaningful[name]]
    
# convocation_name_x_token_dict_meaningful_parent['1_Тропин_Александр_Михайлович']


In [112]:
# to create 2-tokens

conv_x_name_2token_dict = {}

for name in conv_x_name_token_dict_meaningful_parent:
    conv_x_name_2token_dict[name] = []
    for i in range(len(conv_x_name_token_dict_meaningful_parent[name]) - 1):
        conv_x_name_2token_dict[name].append([conv_x_name_token_dict_meaningful_parent[name][i], conv_x_name_token_dict_meaningful_parent[name][i+1]])
    
print(conv_x_name_2token_dict)


{'1_Левин_Андрей': [['активный', 'участник'], ['участник', 'организатор'], ['организатор', 'различный'], ['различный', 'мероприятие'], ['мероприятие', 'воспоминание'], ['воспоминание', 'любимый'], ['любимый', 'школа'], ['школа', 'готовый'], ['готовый', 'работать'], ['работать', 'творить'], ['творить', 'уверенный'], ['уверенный', 'получиться']], '1_Кириллова_Полина': [['нравиться', 'заниматься'], ['заниматься', 'общественный'], ['общественный', 'деятельность'], ['деятельность', 'всячески'], ['всячески', 'пытаться'], ['пытаться', 'расширять'], ['расширять', 'кругозор'], ['кругозор', 'школа'], ['школа', 'организовывать'], ['организовывать', 'различный'], ['различный', 'мероприятие'], ['мероприятие', 'быть'], ['быть', 'сильно'], ['сильно', 'заинтересовать'], ['заинтересовать', 'увлекаться'], ['увлекаться', 'музыка'], ['музыка', 'больший'], ['больший', 'развитие'], ['развитие', 'записаться'], ['записаться', 'академический'], ['академический', 'хор'], ['хор', 'начало'], ['начало', 'заниматьс

In [113]:
token2_dict = {}

for name in conv_x_name_2token_dict:
    for t in conv_x_name_2token_dict[name]:
        token2_dict['_'.join(t)] = {'2-token': t, 'cnt': 0}
        
for name in conv_x_name_2token_dict:
    for t in conv_x_name_2token_dict[name]:
        token2_dict['_'.join(t)]['cnt'] += 1

token2_dict = dict(sorted(token2_dict.items(), key=lambda item: item[1]['cnt'], reverse=True))
token2_dict
# print(convocation_2token_dict)

{'студенческий_совет': {'2-token': ['студенческий', 'совет'], 'cnt': 139},
 'рабочий_группа': {'2-token': ['рабочий', 'группа'], 'cnt': 110},
 'день_мехмат': {'2-token': ['день', 'мехмат'], 'cnt': 57},
 'бытовой_вопрос': {'2-token': ['бытовой', 'вопрос'], 'cnt': 55},
 'день_пифагор': {'2-token': ['день', 'пифагор'], 'cnt': 45},
 'повышенный_стипендия': {'2-token': ['повышенный', 'стипендия'], 'cnt': 43},
 'член_студсовет': {'2-token': ['член', 'студсовет'], 'cnt': 41},
 'студсовет_мехмат': {'2-token': ['студсовет', 'мехмат'], 'cnt': 38},
 'привет_звать': {'2-token': ['привет', 'звать'], 'cnt': 38},
 'жизнь_факультет': {'2-token': ['жизнь', 'факультет'], 'cnt': 36},
 'группа_образование': {'2-token': ['группа', 'образование'], 'cnt': 36},
 'принимать_участие': {'2-token': ['принимать', 'участие'], 'cnt': 34},
 'организация_праздник': {'2-token': ['организация', 'праздник'], 'cnt': 31},
 'участвовать_организация': {'2-token': ['участвовать', 'организация'],
  'cnt': 31},
 'различный_меро

In [257]:
# 2-tokens
# ПЕРЕБРАЛ до >= 6


full_cultmass_2tokens = [
    'день_мехмат', 'день_пифагор', 'организация_праздник', 'участвовать_организация', 'различный_мероприятие', 'различный_мероприятие', 
    'помогать_организация', 'заниматься_организация', 'группа_праздник', 'организация_проведение', 'школа_актив', 'конкурс_группа', 
    'организация_мероприятие', 'организация_различный', 'пифагор_день', 'участие_организация', 'культурно-массовый_мероприятие',
    'посвящение_первокурсник', 'мероприятие_факультет', 'помогать_проведение', 'мероприятие_день', 'мехмат_день', 'проведение_праздник',
    'проведение_день', 'праздник_день', 'посвятой_день', 'организация_культурно-массовый', 'мероприятие_посвятой', 'мехмат_посвящение', 
    'первокурсник_день', 'ночь_мехмат', 'just_dance'
]
full_sport_2tokens = ['спортивный_мероприятие', 'группа_спорт', 'организация_спортивный']
full_partners_2tokens = ['работа_партнёр']

full_rights_fight_2tokens = [
    'проблема_студент', 'студенческий_самоуправление', 'решить_проблема', 'отстаивать_интерес', 'решение_проблема', 'право_студент',
    'отстаивать_право'
]

full_education_2tokens = [
    'группа_образование', 'качество_образование', 'иностранный_язык', 'учебный_процесс', 'учебный_часть', 'встреча_кафедра',
    'встреча_второкурсник', 'качество_преподавание', 'контроль_качество', 'вопрос_образование', 'опрос_качество', 'курс_иностранный'
]
full_infrastructure_2tokens = [
    'бытовой_вопрос', 'группа_бытовой', 'решение_бытовой', 'сбор_макулатура', 'проблема_общежитие', 'улучшение_условие', 
    'бытовой_проблема', 'условие_проживание'
]
full_inform_2tokens = ['группа_оповещение']

full_grants_2tokens = ['повышенный_стипендия', 'распределение_повышенный', 'распределение_стипендия']

full_unversity_level_2tokens = ['студсовет_мгу']

# также интересные:
# главный_организатор, план_работа, быть_активный, факультет_университет, общежитие_гз, ответственный_секретарь, проект_студсовет
# продолжить_деятельность

In [258]:
# считаем, сколько ключевых слов по каждому направлению встретилось в программе кандидата

def get_flag_by_2tokens(conv_x_name_2token_dict, year_no_x_name, full_branch_2tokens):
    branch_flg = 0
    for t in conv_x_name_2token_dict[year_no_x_name]:
        if t in [token2_dict[token]['2-token'] for token in full_branch_2tokens]:
            branch_flg += 1
#             break
    return branch_flg


conv_x_name_weights_2 = {}

for w in convocation_name_x_2token_dict:
    cultmass_w           = get_flag_by_2tokens(conv_x_name_2token_dict, w, full_cultmass_2tokens)
    sport_w              = get_flag_by_2tokens(conv_x_name_2token_dict, w, full_sport_2tokens)
    partners_w           = get_flag_by_2tokens(conv_x_name_2token_dict, w, full_partners_2tokens)
    rights_fight_w       = get_flag_by_2tokens(conv_x_name_2token_dict, w, full_rights_fight_2tokens)
    education_w          = get_flag_by_2tokens(conv_x_name_2token_dict, w, full_education_2tokens)
    infrastructure_w     = get_flag_by_2tokens(conv_x_name_2token_dict, w, full_infrastructure_2tokens)
    inform_w             = get_flag_by_2tokens(conv_x_name_2token_dict, w, full_inform_2tokens)
    grants_w             = get_flag_by_2tokens(conv_x_name_2token_dict, w, full_grants_2tokens)
    university_level_w   = get_flag_by_2tokens(conv_x_name_2token_dict, w, full_unversity_level_2tokens)
    
    conv_x_name_weights_2[w] = {
        'cultmass_w': cultmass_w, 
        'sport_w': sport_w, 
        'partners_w': partners_w, 
        'rights_fight_w': rights_fight_w, 
        'education_w': education_w, 
        'infrastructure_w': infrastructure_w, 
        'inform_w': inform_w, 
        'grants_w': grants_w, 
        'university_level_w': university_level_w
    }

conv_x_name_weights_2

# сделать поиск 2-токенов и т.д., чтобы выявлять "студсовет МГУ", "университетском уровне" и прочее (на примере Глунчадзе)

{'1_Левин_Андрей': {'cultmass_w': 1,
  'sport_w': 0,
  'partners_w': 0,
  'rights_fight_w': 0,
  'education_w': 0,
  'infrastructure_w': 0,
  'inform_w': 0,
  'grants_w': 0,
  'university_level_w': 0},
 '1_Кириллова_Полина': {'cultmass_w': 2,
  'sport_w': 0,
  'partners_w': 0,
  'rights_fight_w': 1,
  'education_w': 0,
  'infrastructure_w': 0,
  'inform_w': 0,
  'grants_w': 0,
  'university_level_w': 0},
 '1_Семенов_Павел': {'cultmass_w': 0,
  'sport_w': 0,
  'partners_w': 0,
  'rights_fight_w': 1,
  'education_w': 0,
  'infrastructure_w': 0,
  'inform_w': 0,
  'grants_w': 0,
  'university_level_w': 0},
 '1_Кузнецова_Алёна': {'cultmass_w': 2,
  'sport_w': 0,
  'partners_w': 0,
  'rights_fight_w': 0,
  'education_w': 0,
  'infrastructure_w': 0,
  'inform_w': 0,
  'grants_w': 0,
  'university_level_w': 0},
 '1_Кунденко_Вадим': {'cultmass_w': 0,
  'sport_w': 0,
  'partners_w': 0,
  'rights_fight_w': 0,
  'education_w': 0,
  'infrastructure_w': 0,
  'inform_w': 0,
  'grants_w': 0,
  'unive

In [259]:
conv_x_name_weights_2_df = pd.DataFrame(conv_x_name_weights_2).transpose()
conv_x_name_weights_2_df

cultmass_w  sport_w  partners_w  \
1_Левин_Андрей                                    1        0           0   
1_Кириллова_Полина                                2        0           0   
1_Семенов_Павел                                   0        0           0   
1_Кузнецова_Алёна                                 2        0           0   
1_Кунденко_Вадим                                  0        0           0   
...                                             ...      ...         ...   
11_Терехов_Михаил_Сергеевич                       0        0           0   
11_Поликарпов_Александр_Валерьевич                0        0           0   
11_Каляев_Тимур_Джанбулатович                     0        0           0   
11_Маммагаджиев_Руслан_Гаджимагомедович           0        0           0   
11_Третьякова_Екатерина_Алексеевна                0        0           0   

                                         rights_fight_w  education_w  \
1_Левин_Андрей                                        0            0   
1_Кириллова_Полина                                    1            0   
1_Семенов_Павел                                       1            0   
1_Кузнецова_Алёна                                     0            0   
1_Кунденко_Вадим                                      0            0   
...                                                 ...          ...   
11_Терехов_Михаил_Сергеевич                           0            0   
11_Поликарпов_Александр_Валерьевич                    0            0   
11_Каляев_Тимур_Джанбулатович                         0            0   
11_Маммагаджиев_Руслан_Гаджимагомедович               0            0   
11_Третьякова_Екатерина_Алексеевна                    0            0   

                                         infrastructure_w  inform_w  grants_w  \
1_Левин_Андрей                                          0         0         0   
1_Кириллова_Полина                                      0         0         0   
1_Семенов_Павел                                         0         0         0   
1_Кузнецова_Алёна                                       0         0         0   
1_Кунденко_Вадим                                        0         0         0   
...                                                   ...       ...       ...   
11_Терехов_Михаил_Сергеевич                             0         0         0   
11_Поликарпов_Александр_Валерьевич                      0         0         0   
11_Каляев_Тимур_Джанбулатович                           0         0         0   
11_Маммагаджиев_Руслан_Гаджимагомедович                 0         0         0   
11_Третьякова_Екатерина_Алексеевна                      0         0         0   

                                         university_level_w  
1_Левин_Андрей                                            0  
1_Кириллова_Полина                                        0  
1_Семенов_Павел                                           0  
1_Кузнецова_Алёна                                         0  
1_Кунденко_Вадим                                          0  
...                                                     ...  
11_Терехов_Михаил_Сергеевич                               0  
11_Поликарпов_Александр_Валерьевич                        0  
11_Каляев_Тимур_Джанбулатович                             0  
11_Маммагаджиев_Руслан_Гаджимагомедович                   0  
11_Третьякова_Екатерина_Алексеевна                        0  

[462 rows x 9 columns]

In [ ]:
# УБРАТЬ КАКИЕ-ТО ПЕРЕСЕЧЕНИЯ МЕЖДУ 1-токенами и 2-токенами

## 4. To set up flags for 1- and 2-TOKENS

In [260]:
# просуммировать количества из двух таблиц

conv_x_name_common_weights_df = conv_x_name_weights_2_df.add(conv_x_name_weights_df, fill_value=0)
conv_x_name_common_weights_df

cultmass_w  education_w  grants_w  \
1_Левин_Андрей                                    2            0       0.0   
1_Кириллова_Полина                                6            0       0.0   
1_Семенов_Павел                                   2            0       0.0   
1_Кузнецова_Алёна                                 4            0       0.0   
1_Кунденко_Вадим                                  0            0       0.0   
...                                             ...          ...       ...   
11_Терехов_Михаил_Сергеевич                       0            0       0.0   
11_Поликарпов_Александр_Валерьевич                0            0       0.0   
11_Каляев_Тимур_Джанбулатович                     0            0       0.0   
11_Маммагаджиев_Руслан_Гаджимагомедович           0            0       0.0   
11_Третьякова_Екатерина_Алексеевна                0            0       0.0   

                                         inform_w  infrastructure_w  \
1_Левин_Андрей                                  0                 0   
1_Кириллова_Полина                              0                 3   
1_Семенов_Павел                                 0                 3   
1_Кузнецова_Алёна                               0                 0   
1_Кунденко_Вадим                                0                 0   
...                                           ...               ...   
11_Терехов_Михаил_Сергеевич                     0                 0   
11_Поликарпов_Александр_Валерьевич              0                 0   
11_Каляев_Тимур_Джанбулатович                   0                 0   
11_Маммагаджиев_Руслан_Гаджимагомедович         0                 0   
11_Третьякова_Екатерина_Алексеевна              0                 0   

                                         partners_w  rights_fight_w  sport_w  \
1_Левин_Андрей                                  0.0               0        0   
1_Кириллова_Полина                              0.0               5        2   
1_Семенов_Павел                                 0.0               6        0   
1_Кузнецова_Алёна                               0.0               1        0   
1_Кунденко_Вадим                                0.0               2        0   
...                                             ...             ...      ...   
11_Терехов_Михаил_Сергеевич                     0.0               0        0   
11_Поликарпов_Александр_Валерьевич              0.0               0        0   
11_Каляев_Тимур_Джанбулатович                   0.0               2        0   
11_Маммагаджиев_Руслан_Гаджимагомедович         0.0               1        0   
11_Третьякова_Екатерина_Алексеевна              0.0               1        0   

                                         university_level_w  
1_Левин_Андрей                                          0.0  
1_Кириллова_Полина                                      0.0  
1_Семенов_Павел                                         0.0  
1_Кузнецова_Алёна                                       0.0  
1_Кунденко_Вадим                                        0.0  
...                                                     ...  
11_Терехов_Михаил_Сергеевич                             0.0  
11_Поликарпов_Александр_Валерьевич                      0.0  
11_Каляев_Тимур_Джанбулатович                           0.0  
11_Маммагаджиев_Руслан_Гаджимагомедович                 0.0  
11_Третьякова_Екатерина_Алексеевна                      0.0  

[462 rows x 9 columns]

In [146]:
# выделить топ-2 направлений по каждому conv_x_name
# что делать при равенстве весов?

# пока только топ-1:
# conv_x_name_common_weights_df_1 = conv_x_name_common_weights_df

# conv_x_name_common_weights_df_1['top_1'] = conv_x_name_common_weights_df_1[list(conv_x_name_common_weights_df)].idxmax(axis=1)
# conv_x_name_common_weights_df_1[:20]



In [261]:
xx = pd.DataFrame(conv_x_name_common_weights_df).T

top_3 = pd.DataFrame(np.zeros((0,3)), columns=['top1','top2','top3'])
rslt = top_3

for conv_x_name in xx.columns:
    df1row = pd.DataFrame(xx.nlargest(3, conv_x_name).index.tolist(), index=['top1','top2','top3']).T
    rslt = pd.concat([rslt, df1row], axis=0)

top_df = rslt.reset_index().drop(['index'], axis=1)
top_df


# xx.nlargest(3, conv_x_name, keep='all') - оставляет всех, занявших не ниже третьего места (КАК НА ВЫБОРАХ НА ПОТОКЕ)

top1              top2              top3
0        cultmass_w       education_w          grants_w
1        cultmass_w    rights_fight_w  infrastructure_w
2    rights_fight_w  infrastructure_w        cultmass_w
3        cultmass_w    rights_fight_w       education_w
4    rights_fight_w        cultmass_w       education_w
..              ...               ...               ...
457      cultmass_w       education_w          grants_w
458      cultmass_w       education_w          grants_w
459  rights_fight_w        cultmass_w       education_w
460  rights_fight_w        cultmass_w       education_w
461  rights_fight_w        cultmass_w       education_w

[462 rows x 3 columns]

In [262]:
# убрать названия, за которыми стоят нули
# названия колонок, в которых нули

def zero_flg(x):
    if x == 0:
        return True
    else:
        return False

rslt1 = pd.DataFrame(np.zeros((0,9)))

for conv_x_name in xx.columns:
    df1row1 = pd.DataFrame(xx[xx[conv_x_name].apply(lambda x: zero_flg(x))].index.tolist()).T
    rslt1 = pd.concat([rslt1, df1row1], axis=0)
rslt1 = rslt1.reset_index().drop(['index'], axis=1)
for i in range(9):
    rslt1 = rslt1.rename(columns={i: 'b'+str(i)})
zero_branches = rslt1

zero_branches


b0           b1        b2                b3                  b4  \
0    education_w     grants_w  inform_w  infrastructure_w          partners_w   
1    education_w     grants_w  inform_w        partners_w  university_level_w   
2    education_w     grants_w  inform_w        partners_w             sport_w   
3    education_w     grants_w  inform_w  infrastructure_w          partners_w   
4     cultmass_w  education_w  grants_w          inform_w    infrastructure_w   
..           ...          ...       ...               ...                 ...   
457   cultmass_w  education_w  grants_w          inform_w    infrastructure_w   
458   cultmass_w  education_w  grants_w          inform_w    infrastructure_w   
459   cultmass_w  education_w  grants_w          inform_w    infrastructure_w   
460   cultmass_w  education_w  grants_w          inform_w    infrastructure_w   
461   cultmass_w  education_w  grants_w          inform_w    infrastructure_w   

                     b5                  b6                  b7  \
0        rights_fight_w             sport_w  university_level_w   
1                   NaN                 NaN                 NaN   
2    university_level_w                 NaN                 NaN   
3               sport_w  university_level_w                 NaN   
4            partners_w             sport_w  university_level_w   
..                  ...                 ...                 ...   
457          partners_w      rights_fight_w             sport_w   
458          partners_w      rights_fight_w             sport_w   
459          partners_w             sport_w  university_level_w   
460          partners_w             sport_w  university_level_w   
461          partners_w             sport_w  university_level_w   

                     b8  
0                   NaN  
1                   NaN  
2                   NaN  
3                   NaN  
4                   NaN  
..                  ...  
457  university_level_w  
458  university_level_w  
459                 NaN  
460                 NaN  
461                 NaN  

[462 rows x 9 columns]

In [263]:
# ЗАДЖОЙНИТЬ ПО ИНДЕКСУ

conv_x_name_common_weights_df_2 = conv_x_name_common_weights_df.reset_index().rename(columns={'index':'conv_x_name'})
# conv_x_name_common_weights_df_2

conv_x_name_common_weights_df_3 = conv_x_name_common_weights_df_2.join(top_df)
# conv_x_name_common_weights_df_3 = pd.merge(conv_x_name_common_weights_df_2, top_df, left_index=True, right_index=True)
# conv_x_name_common_weights_df_3 = pd.concat([conv_x_name_common_weights_df_2, top_df], axis=1)
# conv_x_name_common_weights_df_3

conv_x_name_common_weights_df_4 = conv_x_name_common_weights_df_3.join(zero_branches)

conv_x_name_common_weights_df_4


conv_x_name  cultmass_w  education_w  \
0                             1_Левин_Андрей           2            0   
1                         1_Кириллова_Полина           6            0   
2                            1_Семенов_Павел           2            0   
3                          1_Кузнецова_Алёна           4            0   
4                           1_Кунденко_Вадим           0            0   
..                                       ...         ...          ...   
457              11_Терехов_Михаил_Сергеевич           0            0   
458       11_Поликарпов_Александр_Валерьевич           0            0   
459            11_Каляев_Тимур_Джанбулатович           0            0   
460  11_Маммагаджиев_Руслан_Гаджимагомедович           0            0   
461       11_Третьякова_Екатерина_Алексеевна           0            0   

     grants_w  inform_w  infrastructure_w  partners_w  rights_fight_w  \
0         0.0         0                 0         0.0               0   
1         0.0         0                 3         0.0               5   
2         0.0         0                 3         0.0               6   
3         0.0         0                 0         0.0               1   
4         0.0         0                 0         0.0               2   
..        ...       ...               ...         ...             ...   
457       0.0         0                 0         0.0               0   
458       0.0         0                 0         0.0               0   
459       0.0         0                 0         0.0               2   
460       0.0         0                 0         0.0               1   
461       0.0         0                 0         0.0               1   

     sport_w  university_level_w  ...              top3           b0  \
0          0                 0.0  ...          grants_w  education_w   
1          2                 0.0  ...  infrastructure_w  education_w   
2          0                 0.0  ...        cultmass_w  education_w   
3          0                 0.0  ...       education_w  education_w   
4          0                 0.0  ...       education_w   cultmass_w   
..       ...                 ...  ...               ...          ...   
457        0                 0.0  ...          grants_w   cultmass_w   
458        0                 0.0  ...          grants_w   cultmass_w   
459        0                 0.0  ...       education_w   cultmass_w   
460        0                 0.0  ...       education_w   cultmass_w   
461        0                 0.0  ...       education_w   cultmass_w   

              b1        b2                b3                  b4  \
0       grants_w  inform_w  infrastructure_w          partners_w   
1       grants_w  inform_w        partners_w  university_level_w   
2       grants_w  inform_w        partners_w             sport_w   
3       grants_w  inform_w  infrastructure_w          partners_w   
4    education_w  grants_w          inform_w    infrastructure_w   
..           ...       ...               ...                 ...   
457  education_w  grants_w          inform_w    infrastructure_w   
458  education_w  grants_w          inform_w    infrastructure_w   
459  education_w  grants_w          inform_w    infrastructure_w   
460  education_w  grants_w          inform_w    infrastructure_w   
461  education_w  grants_w          inform_w    infrastructure_w   

                     b5                  b6                  b7  \
0        rights_fight_w             sport_w  university_level_w   
1                   NaN                 NaN                 NaN   
2    university_level_w                 NaN                 NaN   
3               sport_w  university_level_w                 NaN   
4            partners_w             sport_w  university_level_w   
..                  ...                 ...                 ...   
457          partners_w      rights_fight_w             sport_w   
458          partners_w      rights_fight_w             sport

In [264]:
df = conv_x_name_common_weights_df_4
for top in ['top1', 'top2', 'top3']:
    df[top+'_check'] = np.where(((df[top] != df.b0) & (df[top] != df.b1) & (df[top] != df.b2) & (df[top] != df.b3) & (df[top] != df.b4) & (df[top] != df.b5) & (df[top] != df.b6) & (df[top] != df.b7) & (df[top] != df.b8)), 1, 0)
df = df.drop(['b0','b1','b2','b3','b4','b5','b6','b7','b8'],axis=1)
# df
for top in ['top1', 'top2', 'top3']:
    df[top] = np.where((df[top+'_check'] == 0), None, df[top].apply(lambda x: x[:-2]))
# df = df.drop(['top1_check','top2_check','top3_check'],axis=1)
conv_x_name_top_branches_df = df[['conv_x_name','top1','top2','top3']]

conv_x_name_top_branches_df


conv_x_name          top1            top2  \
0                             1_Левин_Андрей      cultmass            None   
1                         1_Кириллова_Полина      cultmass    rights_fight   
2                            1_Семенов_Павел  rights_fight  infrastructure   
3                          1_Кузнецова_Алёна      cultmass    rights_fight   
4                           1_Кунденко_Вадим  rights_fight            None   
..                                       ...           ...             ...   
457              11_Терехов_Михаил_Сергеевич          None            None   
458       11_Поликарпов_Александр_Валерьевич          None            None   
459            11_Каляев_Тимур_Джанбулатович  rights_fight            None   
460  11_Маммагаджиев_Руслан_Гаджимагомедович  rights_fight            None   
461       11_Третьякова_Екатерина_Алексеевна  rights_fight            None   

               top3  
0              None  
1    infrastructure  
2          cultmass  
3              None  
4              None  
..              ...  
457            None  
458            None  
459            None  
460            None  
461            None  

[462 rows x 4 columns]

In [269]:
# ПРОВЕРКА: чьи программы не попали ни в одну категорию

df[df['top1'].isna()]

conv_x_name  cultmass_w  education_w  grants_w  \
6              1_Глухова_Алёна_Олеговна           0            0       0.0   
11      1_Артамонова_Мария_Владимировна           0            0       0.0   
14            1_Чернодед_Антон_Игоревич           0            0       0.0   
16         1_Савушкин_Никита_Максимович           0            0       0.0   
19        2_Габидов_Александр_Сергеевич           0            0       0.0   
..                                  ...         ...          ...       ...   
452          11_Заводян_Михаил_Игоревич           0            0       0.0   
453         11_Уваров_Андрей_Михайлович           0            0       0.0   
456     11_Мазитова_Вероника_Рустэмовна           0            0       0.0   
457         11_Терехов_Михаил_Сергеевич           0            0       0.0   
458  11_Поликарпов_Александр_Валерьевич           0            0       0.0   

     inform_w  infrastructure_w  partners_w  rights_fight_w  sport_w  \
6           0                 0         0.0               0        0   
11          0                 0         0.0               0        0   
14          0                 0         0.0               0        0   
16          0                 0         0.0               0        0   
19          0                 0         0.0               0        0   
..        ...               ...         ...             ...      ...   
452         0                 0         0.0               0        0   
453         0                 0         0.0               0        0   
456         0                 0         0.0               0        0   
457         0                 0         0.0               0        0   
458         0                 0         0.0               0        0   

     university_level_w  top1  top2  top3  top1_check  top2_check  top3_check  
6                   0.0  None  None  None           0           0           0  
11                  0.0  None  None  None           0           0           0  
14                  0.0  None  None  None           0           0           0  
16                  0.0  None  None  None           0           0           0  
19                  0.0  None  None  None           0           0           0  
..                  ...   ...   ...   ...         ...         ...         ...  
452                 0.0  None  None  None           0           0           0  
453                 0.0  None  None  None           0           0           0  
456                 0.0  None  None  None           0           0           0  
457                 0.0  None  None  None           0           0           0  
458                 0.0  None  None  None           0           0           0  

[75 rows x 16 columns]

In [ ]:
# ДАЛЕЕ ДЕЛАЕМ ФЛАГИ, НО МБ ЛУЧШЕ ОСТАВИТЬ ВЕСА

In [93]:

for name_flg in list(convocation_name_x_flags_df):
    convocation_name_x_flags_df[name_flg] = convocation_name_x_flags_df[name_flg].apply(lambda x: np.sign(x))

convocation_name_x_flags_df

# convocation_name_x_flags_df2 = convocation_name_x_flags_df
# convocation_name_x_flags_df2


cultmass_flg  sport_flg  \
1_Левин_Андрей                                      1          0   
1_Кириллова_Полина                                  1          1   
1_Семенов_Павел                                     1          0   
1_Кузнецова_Алёна                                   1          0   
1_Кунденко_Вадим                                    0          0   
...                                               ...        ...   
11_Терехов_Михаил_Сергеевич                         0          0   
11_Поликарпов_Александр_Валерьевич                  0          0   
11_Каляев_Тимур_Джанбулатович                       0          0   
11_Маммагаджиев_Руслан_Гаджимагомедович             0          0   
11_Третьякова_Екатерина_Алексеевна                  0          0   

                                         rights_fight_flg  education_flg  \
1_Левин_Андрей                                          0              0   
1_Кириллова_Полина                                      1              0   
1_Семенов_Павел                                         1              0   
1_Кузнецова_Алёна                                       0              0   
1_Кунденко_Вадим                                        1              0   
...                                                   ...            ...   
11_Терехов_Михаил_Сергеевич                             0              0   
11_Поликарпов_Александр_Валерьевич                      0              0   
11_Каляев_Тимур_Джанбулатович                           1              0   
11_Маммагаджиев_Руслан_Гаджимагомедович                 1              0   
11_Третьякова_Екатерина_Алексеевна                      0              0   

                                         infrastructure_flg  inform_flg  
1_Левин_Андрей                                            0           0  
1_Кириллова_Полина                                        1           0  
1_Семенов_Павел                                           1           0  
1_Кузнецова_Алёна                                         0           0  
1_Кунденко_Вадим                                          0           0  
...                                                     ...         ...  
11_Терехов_Михаил_Сергеевич                               0           0  
11_Поликарпов_Александр_Валерьевич                        0           0  
11_Каляев_Тимур_Джанбулатович                             0           0  
11_Маммагаджиев_Руслан_Гаджимагомедович                   0           0  
11_Третьякова_Екатерина_Алексеевна                        0           0  

[462 rows x 6 columns]

In [41]:

keke = pd.DataFrame(data=convocation_name_x_flags_df2.sum())
keke.T

cultmass_flg2  sport_flg2  rights_fight_flg2  education_flg2  \
0            219          33                153              64   

   infrastructure_flg2  inform_flg2  
0                   75           52

In [42]:
convocation_name_x_flags_df3 = convocation_name_x_flags_df2.reset_index().rename(columns={'index':'conv_x_name'})
convocation_name_x_flags_df3


conv_x_name  cultmass_flg2  sport_flg2  \
0                             1_Левин_Андрей              1           0   
1                         1_Кириллова_Полина              1           1   
2                            1_Семенов_Павел              1           0   
3                          1_Кузнецова_Алёна              1           0   
4                           1_Кунденко_Вадим              0           0   
..                                       ...            ...         ...   
457              11_Терехов_Михаил_Сергеевич              0           0   
458       11_Поликарпов_Александр_Валерьевич              0           0   
459            11_Каляев_Тимур_Джанбулатович              0           0   
460  11_Маммагаджиев_Руслан_Гаджимагомедович              0           0   
461       11_Третьякова_Екатерина_Алексеевна              0           0   

     rights_fight_flg2  education_flg2  infrastructure_flg2  inform_flg2  
0                    0               0                    0            0  
1                    1               0                    0            0  
2                    1               0                    0            0  
3                    0               0                    0            0  
4                    1               0                    0            0  
..                 ...             ...                  ...          ...  
457                  0               0                    0            0  
458                  0               0                    0            0  
459                  1               0                    0            0  
460                  1               0                    0            0  
461                  0               0                    0            0  

[462 rows x 7 columns]

In [43]:
convocation_name_x_flags_df3.to_csv('ssmm_program_classification.csv', sep='\t', encoding='utf-8', index=False)
convocation_name_x_flags_df3.to_csv('library: main/ssmm_program_classification.csv', sep='\t', encoding='utf-8', index=False)


In [44]:
# ИЛИ ТАК

convocation_name_x_flags_df4 = convocation_name_x_flags_df2.reset_index().rename(columns={'index': 'conv_x_name'})
convocation_name_x_flags_df4['convocation_no'] = convocation_name_x_flags_df4['conv_x_name'].apply(lambda x: int(x[0:x.index('_')]))
convocation_name_x_flags_df4.head()

conv_x_name  cultmass_flg2  sport_flg2  rights_fight_flg2  \
0      1_Левин_Андрей              1           0                  0   
1  1_Кириллова_Полина              1           1                  1   
2     1_Семенов_Павел              1           0                  1   
3   1_Кузнецова_Алёна              1           0                  0   
4    1_Кунденко_Вадим              0           0                  1   

   education_flg2  infrastructure_flg2  inform_flg2  convocation_no  
0               0                    0            0               1  
1               0                    0            0               1  
2               0                    0            0               1  
3               0                    0            0               1  
4               0                    0            0               1

In [45]:
convocation_name_x_flags_df4.groupby(['convocation_no']).sum()

cultmass_flg2  sport_flg2  rights_fight_flg2  education_flg2  \
convocation_no                                                                 
1                          11           2                  6               1   
2                          11           0                  5               4   
3                          17           2                 10               3   
4                          31           5                 15               9   
5                          27           9                 14              14   
6                          29           4                 23               7   
7                          16           2                 12               3   
8                          19           3                  9               4   
9                          23           2                 14               1   
10                         22           2                 31              12   
11                         13           2                 14               6   

                infrastructure_flg2  inform_flg2  
convocation_no                                    
1                                 2            0  
2                                 4            5  
3                                 7            3  
4                                 9            6  
5                                12           13  
6                                15            6  
7                                 3            3  
8                                 7            1  
9                                 3            1  
10                                8           10  
11                                5            4

## 2. To create 2-TOKENS

{'1_Левин_Андрей': [['активный', 'участник'], ['участник', 'организатор'], ['организатор', 'различный'], ['различный', 'мероприятие'], ['мероприятие', 'воспоминание'], ['воспоминание', 'любимый'], ['любимый', 'школа'], ['школа', 'готовый'], ['готовый', 'работать'], ['работать', 'творить'], ['творить', 'уверенный'], ['уверенный', 'получиться']], '1_Кириллова_Полина': [['нравиться', 'заниматься'], ['заниматься', 'общественный'], ['общественный', 'деятельность'], ['деятельность', 'всячески'], ['всячески', 'пытаться'], ['пытаться', 'расширять'], ['расширять', 'кругозор'], ['кругозор', 'школа'], ['школа', 'организовывать'], ['организовывать', 'различный'], ['различный', 'мероприятие'], ['мероприятие', 'быть'], ['быть', 'сильно'], ['сильно', 'заинтересовать'], ['заинтересовать', 'увлекаться'], ['увлекаться', 'музыка'], ['музыка', 'больший'], ['больший', 'развитие'], ['развитие', 'записаться'], ['записаться', 'академический'], ['академический', 'хор'], ['хор', 'начало'], ['начало', 'заниматьс

{'студенческий_совет': {'2-token': ['студенческий', 'совет'], 'cnt': 139},
 'рабочий_группа': {'2-token': ['рабочий', 'группа'], 'cnt': 110},
 'день_мехмат': {'2-token': ['день', 'мехмат'], 'cnt': 57},
 'бытовой_вопрос': {'2-token': ['бытовой', 'вопрос'], 'cnt': 55},
 'день_пифагор': {'2-token': ['день', 'пифагор'], 'cnt': 45},
 'повышенный_стипендия': {'2-token': ['повышенный', 'стипендия'], 'cnt': 43},
 'член_студсовет': {'2-token': ['член', 'студсовет'], 'cnt': 41},
 'студсовет_мехмат': {'2-token': ['студсовет', 'мехмат'], 'cnt': 38},
 'привет_звать': {'2-token': ['привет', 'звать'], 'cnt': 38},
 'жизнь_факультет': {'2-token': ['жизнь', 'факультет'], 'cnt': 36},
 'группа_образование': {'2-token': ['группа', 'образование'], 'cnt': 36},
 'принимать_участие': {'2-token': ['принимать', 'участие'], 'cnt': 34},
 'организация_праздник': {'2-token': ['организация', 'праздник'], 'cnt': 31},
 'участвовать_организация': {'2-token': ['участвовать', 'организация'],
  'cnt': 31},
 'различный_меро

{'1_Левин_Андрей': {'cultmass_flg': 1,
  'sport_flg': 0,
  'partners_flg': 0,
  'rights_fight_flg': 0,
  'education_flg': 0,
  'infrastructure_flg': 0,
  'inform_flg': 0,
  'grants_flg': 0,
  'university_level_flg': 0},
 '1_Кириллова_Полина': {'cultmass_flg': 2,
  'sport_flg': 0,
  'partners_flg': 0,
  'rights_fight_flg': 0,
  'education_flg': 0,
  'infrastructure_flg': 0,
  'inform_flg': 0,
  'grants_flg': 0,
  'university_level_flg': 0},
 '1_Семенов_Павел': {'cultmass_flg': 0,
  'sport_flg': 0,
  'partners_flg': 0,
  'rights_fight_flg': 0,
  'education_flg': 0,
  'infrastructure_flg': 0,
  'inform_flg': 0,
  'grants_flg': 0,
  'university_level_flg': 0},
 '1_Кузнецова_Алёна': {'cultmass_flg': 2,
  'sport_flg': 0,
  'partners_flg': 0,
  'rights_fight_flg': 0,
  'education_flg': 0,
  'infrastructure_flg': 0,
  'inform_flg': 0,
  'grants_flg': 0,
  'university_level_flg': 0},
 '1_Кунденко_Вадим': {'cultmass_flg': 0,
  'sport_flg': 0,
  'partners_flg': 0,
  'rights_fight_flg': 0,
  'educ

cultmass_flg  sport_flg  \
1_Левин_Андрей                                      1          0   
1_Кириллова_Полина                                  2          0   
1_Семенов_Павел                                     0          0   
1_Кузнецова_Алёна                                   2          0   
1_Кунденко_Вадим                                    0          0   
...                                               ...        ...   
11_Терехов_Михаил_Сергеевич                         0          0   
11_Поликарпов_Александр_Валерьевич                  0          0   
11_Каляев_Тимур_Джанбулатович                       0          0   
11_Маммагаджиев_Руслан_Гаджимагомедович             0          0   
11_Третьякова_Екатерина_Алексеевна                  0          0   

                                         partners_flg  rights_fight_flg  \
1_Левин_Андрей                                      0                 0   
1_Кириллова_Полина                                  0                 0   
1_Семенов_Павел                                     0                 0   
1_Кузнецова_Алёна                                   0                 0   
1_Кунденко_Вадим                                    0                 0   
...                                               ...               ...   
11_Терехов_Михаил_Сергеевич                         0                 0   
11_Поликарпов_Александр_Валерьевич                  0                 0   
11_Каляев_Тимур_Джанбулатович                       0                 0   
11_Маммагаджиев_Руслан_Гаджимагомедович             0                 0   
11_Третьякова_Екатерина_Алексеевна                  0                 0   

                                         education_flg  infrastructure_flg  \
1_Левин_Андрей                                       0                   0   
1_Кириллова_Полина                                   0                   0   
1_Семенов_Павел                                      0                   0   
1_Кузнецова_Алёна                                    0                   0   
1_Кунденко_Вадим                                     0                   0   
...                                                ...                 ...   
11_Терехов_Михаил_Сергеевич                          0                   0   
11_Поликарпов_Александр_Валерьевич                   0                   0   
11_Каляев_Тимур_Джанбулатович                        0                   0   
11_Маммагаджиев_Руслан_Гаджимагомедович              0                   0   
11_Третьякова_Екатерина_Алексеевна                   0                   0   

                                         inform_flg  grants_flg  \
1_Левин_Андрей                                    0           0   
1_Кириллова_Полина                                0           0   
1_Семенов_Павел                                   0           0   
1_Кузнецова_Алёна                                 0           0   
1_Кунденко_Вадим                                  0           0   
...                                             ...         ...   
11_Терехов_Михаил_Сергеевич                       0           0   
11_Поликарпов_Александр_Валерьевич                0           0   
11_Каляев_Тимур_Джанбулатович                     0           0   
11_Маммагаджиев_Руслан_Гаджимагомедович           0           0   
11_Третьякова_Екатерина_Алексеевна                0           0   

                                         university_level_flg  
1_Левин_Андрей                                              0  
1_Кириллова_Полина                                          0  
1_Семенов_Павел                                             0  
1_Кузнецова_Алёна                                           0  
1_Кунденко_Вадим                                            0  
...                                                       ...  
11_Терехов_Михаил_Сергеевич                                 0  
11_Поликарпов_Александр_Валерьевич                          0  
11_Ка

In [ ]:
def n_grams(tokens, n=2):
    return list(zip(*[tokens[i: len(tokens) - n + i + 1] for i in range(n)]))

print(n_grams('язык', n=2))

In [ ]:
from nltk import ngrams